In [9]:

# display it inline, and optionally run YOLO inference if you set RUN_INFERENCE = True.
import os, glob, shutil
from pathlib import Path
from IPython.display import HTML
from base64 import b64encode

# ---------- USER OPTIONS ----------
RUN_INFERENCE = False   # set to True if you want the cell to run YOLO inference too (may take time)
CONF_THRESH = 0.35
IMG_SIZE = 640
# ----------------------------------

# 1) Search for video files in common places
search_roots = [Path("/mnt/data"), Path("/content"), Path.home(), Path("/content/drive"), Path("/content/drive/MyDrive")]
patterns = ["*.mp4","*.MP4","*.mov","*.avi"]
candidates = []
for root in search_roots:
    try:
        for pat in patterns:
            for p in root.rglob(pat):
                candidates.append(p)
    except Exception:
        pass

candidates = sorted(set(candidates), key=lambda p: str(p).lower())
print(f"Found {len(candidates)} candidate video file(s):")
for i,p in enumerate(candidates[:50],1):
    print(f"{i}. {p} (size={p.stat().st_size if p.exists() else 'N/A'})")

if not candidates:
    print("\nNo video files found in the usual locations.")
    print("If you uploaded via the notebook UI, open the left Files pane, re-upload the video there,")
    print("or upload to /content using: files.upload() or mount your Drive and copy the file into /content.")
else:
    # choose first candidate (you can change index if needed)
    chosen = candidates[0]
    safe_dst = Path("/content/test_video.mp4")
    try:
        shutil.copy(chosen, safe_dst)
        print(f"\nCopied:\n  {chosen}\n→ {safe_dst}")
    except Exception as e:
        print("Could not copy to /content, will try using original path:", e)
        safe_dst = chosen

    # 2) Display video inline
    p = str(safe_dst)
    if not Path(p).exists():
        print("ERROR: chosen file not found at", p)
    else:
        print("\nDisplaying video inline (may take a few seconds to load in notebook):", p)
        mp4 = open(p,'rb').read()
        data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
        display(HTML(f'<video width=720 controls src="{data_url}"></video>'))

    # 3) Optional: Run YOLO inference if requested
    if RUN_INFERENCE:
        try:
            from ultralytics import YOLO
            print("\nSearching for trained weights (best.pt / last.pt) under /content/road_safety_project...")
            weight_candidates = glob.glob("/content/road_safety_project/runs/**/best*.pt", recursive=True) + \
                                glob.glob("/content/road_safety_project/runs/**/last*.pt", recursive=True)
            weights = weight_candidates[0] if weight_candidates else "yolov8n.pt"
            print("Using weights:", weights)
            model = YOLO(weights)
            print("Running inference (this may take time)...")
            out = model.predict(source=p, conf=CONF_THRESH, imgsz=IMG_SIZE, save=True)
            # find latest detect folder and copy annotated output to /mnt/data for easy download
            detect_dirs = sorted(glob.glob("runs/detect/*"), key=os.path.getmtime)
            if detect_dirs:
                latest = Path(detect_dirs[-1])
                mp4s = list(latest.rglob("*.mp4"))
                if mp4s:
                    dst = Path("/mnt/data") / mp4s[0].name
                    shutil.copy(mp4s[0], dst)
                    print("Annotated mp4 copied to:", dst)
                else:
                    dstfolder = Path("/mnt/data") / latest.name
                    if dstfolder.exists():
                        shutil.rmtree(dstfolder)
                    shutil.copytree(latest, dstfolder)
                    print("Annotated folder copied to:", dstfolder)
            else:
                print("No runs/detect outputs found. Check ultralytics logs above.")
        except Exception as e:
            print("Inference error:", e)


Found 8 candidate video file(s):
1. /content/Cars in Highway Traffic (FREE STOCK VIDEO) (1).mp4 (size=5153120)
2. /content/Cars in Highway Traffic (FREE STOCK VIDEO).mp4 (size=5153120)
3. /content/road_safety_project/predict/Cars in Highway Traffic (FREE STOCK VIDEO) (1).avi (size=46567490)
4. /content/runs/detect/predict/Cars in Highway Traffic (FREE STOCK VIDEO) (1).avi (size=46567490)
5. /content/runs/detect/predict2/test_video.avi (size=46567490)
6. /content/test_video.mp4 (size=5153120)
7. /mnt/data/predict2/test_video.avi (size=46567490)
8. /root/.julia/packages/FileIO/EI2b8/test/files/bees.avi (size=786866)

Copied:
  /content/Cars in Highway Traffic (FREE STOCK VIDEO) (1).mp4
→ /content/test_video.mp4

Displaying video inline (may take a few seconds to load in notebook): /content/test_video.mp4


In [10]:
# Paste & run this cell (one go). It will:
# 1) run quick per-frame checks to show predicted classes for first 5 frames
# 2) run full inference with pretrained yolov8n.pt and save annotated output
# 3) copy annotated mp4 to /content/test_video_pred.mp4 and display inline
from ultralytics import YOLO
from pathlib import Path
import glob, shutil, os, sys, math
from IPython.display import HTML, display
from base64 import b64encode

VIDEO = "/content/test_video.mp4"   # already created earlier by you
CONF = 0.25                        # lower confidence to catch more detections
IMGSZ = 640

if not Path(VIDEO).exists():
    raise FileNotFoundError(f"Video not found at {VIDEO}. Re-run the earlier cell that copied the upload to /content/test_video.mp4")

print("Using video:", VIDEO)
print("Loading pretrained COCO weights (yolov8n.pt)...")
model = YOLO("yolov8n.pt")  # pretrained on COCO (includes 'car', 'truck', 'person', 'motorbike' etc.)

# 1) Print summary detections for first few frames (stream mode)
print("\n--- sample detections from first 5 frames (class id : box count) ---")
frame_count = 0
try:
    for r in model.predict(source=VIDEO, stream=True, conf=CONF, imgsz=IMGSZ):  # stream yields per-frame Results
        boxes = r.boxes  # ultralytics Boxes object
        # each box has .cls (tensor) and .xyxy etc.
        classes = [int(x) for x in boxes.cls.tolist()] if boxes is not None and len(boxes) else []
        # count by class
        cc = {}
        for c in classes:
            cc[c] = cc.get(c, 0) + 1
        print(f"frame {frame_count}: detections:", cc, "; total:", len(classes))
        frame_count += 1
        if frame_count >= 5:
            break
except Exception as e:
    print("Error while streaming frames for quick check:", e)

# 2) Run full inference and save annotated output (Ultralytics writes to runs/detect/)
print("\nRunning full inference and saving annotated outputs (this may take a while)...")
res = model.predict(source=VIDEO, conf=CONF, imgsz=IMGSZ, save=True)  # save=True writes annotated outputs to runs/detect/

# 3) Find latest runs/detect output and copy mp4 (or folder) to /content for easy access
detect_dirs = sorted(glob.glob("runs/detect/*"), key=os.path.getmtime)
if not detect_dirs:
    print("No detect outputs found in runs/detect. Check logs above.")
else:
    latest = Path(detect_dirs[-1])
    print("Latest detect folder:", latest)
    mp4s = list(latest.rglob("*.mp4"))
    dst = None
    if mp4s:
        src = mp4s[0]
        dst = Path("/content/test_video_pred.mp4")
        shutil.copy(src, dst)
        print("Annotated video copied to:", dst)
    else:
        # Ultralytics sometimes saves images only — zip/copy folder
        dst = Path("/content") / latest.name
        if dst.exists():
            shutil.rmtree(dst)
        shutil.copytree(latest, dst)
        print("Annotated folder copied to:", dst)

    # display annotated result inline if mp4 exists
    if dst and dst.exists() and dst.suffix == ".mp4":
        print("\nDisplaying annotated video inline (might take a few seconds to load)...")
        mp4 = open(dst,'rb').read()
        data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
        display(HTML(f'<video width=720 controls src="{data_url}"></video>'))
    else:
        print("\nNo annotated mp4 found. Check the copied folder:", dst)
        # show a sample annotated image if present
        jpgs = list(Path(dst).rglob("*.jpg")) if dst.exists() else []
        if jpgs:
            sample = str(jpgs[0])
            display(HTML(f'<img src="data:image/jpeg;base64,{b64encode(open(sample,"rb").read()).decode()}" width="720">'))


Using video: /content/test_video.mp4
Loading pretrained COCO weights (yolov8n.pt)...

--- sample detections from first 5 frames (class id : box count) ---

video 1/1 (frame 1/1800) /content/test_video.mp4: 384x640 1 person, 15 cars, 1 bus, 1 truck, 16.3ms
frame 0: detections: {2: 15, 7: 1, 5: 1, 0: 1} ; total: 18
video 1/1 (frame 2/1800) /content/test_video.mp4: 384x640 1 person, 16 cars, 1 bus, 1 truck, 7.1ms
frame 1: detections: {2: 16, 7: 1, 0: 1, 5: 1} ; total: 19
video 1/1 (frame 3/1800) /content/test_video.mp4: 384x640 1 person, 15 cars, 1 bus, 2 trucks, 6.0ms
frame 2: detections: {2: 15, 7: 2, 5: 1, 0: 1} ; total: 19
video 1/1 (frame 4/1800) /content/test_video.mp4: 384x640 14 cars, 1 bus, 1 truck, 6.1ms
frame 3: detections: {2: 14, 7: 1, 5: 1} ; total: 16
video 1/1 (frame 5/1800) /content/test_video.mp4: 384x640 1 person, 14 cars, 1 bus, 2 trucks, 6.1ms
frame 4: detections: {2: 14, 7: 2, 0: 1, 5: 1} ; total: 18

Running full inference and saving annotated outputs (this may take